In [25]:
import chart_studio.plotly as py
import numpy as np
import plotly
import pandas as pd
import sklearn.manifold
import plotly.graph_objs as go

## Load data
The data should be a numpy distances matrix. It should be symmetric and have 0-diagonal.

In [105]:
data = np.load('./flip_MDS_run1.npy')

## Choose MDS method

In [140]:
choice = 'TSNE'

In [141]:
if choice == 'TSNE':
    X_embedded = sklearn.manifold.TSNE(n_components=2).fit_transform(data)
if choice == 'SMACOF':
    X_embedded,_,_= sklearn.manifold.mds.smacof(data,
        metric=True,
        n_components=2,
        init=None,
        n_init=8,
        n_jobs=None,
        max_iter=100,
        verbose=0,
        eps=0.001,
        random_state=None,
        return_n_iter=False,
    )

## Let's plot

In [143]:
plotly.offline.init_notebook_mode(connected=True)

In [149]:
dataset = X_embedded

x = X_embedded[:,0]
y = X_embedded[:,1]

N = len(X_embedded)
steps = np.array(range(N))
xm = np.min(x)-1
xM = np.max(x)+1

ym = np.min(y)-1
yM = np.max(y)+1

# make figure
fig_dict = {
    "data": [],
    "layout": {},
    "frames": []
}

# fill in most of layout
fig_dict["layout"]["xaxis"] = {"range": [xm, xM], "title": "x"}
fig_dict["layout"]["yaxis"] = {"title": "y", "range": [ym, yM]}
fig_dict["layout"]["hovermode"] = "closest"
fig_dict["layout"]["sliders"] = {
    "args": [
        "transition", {
            "duration": 200,
            "easing": "cubic-in-out"
        }
    ],
    "initialValue": '0',
    "plotlycommand": "animate",
    "values": steps,
    "visible": True
}

fig_dict["layout"]["updatemenus"] = [
    {
        "buttons": [
            {
                "args": [None, {"frame": {"duration": 500, "redraw": False},
                                "fromcurrent": True, "transition": {"duration": 300,
                                                                    "easing": "quadratic-in-out"}}],
                "label": "Play",
                "method": "animate"
            },
            {
                "args": [[None], {"frame": {"duration": 0, "redraw": False},
                                  "mode": "immediate",
                                  "transition": {"duration": 0}}],
                "label": "Pause",
                "method": "animate"
            }
        ],
        "direction": "left",
        "pad": {"r": 10, "t": 87},
        "showactive": False,
        "type": "buttons",
        "x": 0.1,
        "xanchor": "right",
        "y": 0,
        "yanchor": "top"
    }
]

sliders_dict = {
    "active": 0,
    "yanchor": "top",
    "xanchor": "left",
    "currentvalue": {
        "font": {"size": 10},
        "prefix": "Step:",
        "visible": True,
        "xanchor": "right"
    },
    "transition": {"duration": 200, "easing": "cubic-in-out"},
    "pad": {"b": 10, "t": 50},
    "len": 0.9,
    "x": 0.1,
    "y": 0,
    "steps": []
}


data_dict = {
    "x": list(x),
    "y": list(y),
    "mode": "markers",
    "text": list(steps.astype(str)),
    "marker": {
        "size": 10, "color" : "blue"
    },
}
#fig_dict["data"].append(data_dict)
fig_dict["data"].append(data_dict) #somehow we have to put this twice in order to have the collection of points in the background
# make frames
for step in steps:
    frame = {"data": [], "name": str(step)}

    data_dict ={
        "x": [x[step]],
        "y": [y[step]],
        "mode": "markers",
        "text": list(step.astype(str)),
        "marker": {
            "size": 10, "color" : "red"
        },
    }
    test ={
    "x": list(x),
    "y": list(y),
    "mode": "markers",
    "text": list(steps.astype(str)),
    "marker": {
        "size": 5, "color" : "blue"
    }
    }
    frame["data"].append(data_dict)
    frame["data"].append(test)
    fig_dict["frames"].append(frame)
    slider_step = {"args": [
        [step],
        {"frame": {"duration": 300, "redraw": False},
         "mode": "immediate",
         "transition": {"duration": 300}}
    ],
        "label": str(step),
        "method": "animate"}
    sliders_dict["steps"].append(slider_step)


fig_dict["layout"]["sliders"] = [sliders_dict]

fig = go.Figure(fig_dict)

fig.show()

In [135]:
fig = go.Figure(
    data=[go.Scatter(x=X_embedded[:,0], y=X_embedded[:,1],
                     mode="markers",
                     marker=dict(size=2, color="blue"), text = data_['index']),
          go.Scatter(x=X_embedded[:,0], y=X_embedded[:,1],
                     mode="markers",
                     marker=dict(size=2, color="blue"), text = data_['index'])],
    layout=go.Layout(
        xaxis=dict(range=[xm, xM], autorange=False, zeroline=False),
        yaxis=dict(range=[ym, yM], autorange=False, zeroline=False),
        title_text="t-SNE on MC recom ", hovermode="closest",
        updatemenus=[dict(type="buttons",
                          buttons=[dict(label="Play",
                                        method="animate",
                                        args=[None])])]),
    frames=[go.Frame(
        data=[go.Scatter(
            x=[X_embedded[k,0]],
            y=[X_embedded[k,1]],
            mode="markers",
            marker=dict(color="red", size=10))])
        for k in range(N)]
)



In [136]:
fig.show()

In [50]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation

fig, ax = plt.subplots()
xdata, ydata = [], []
ln, = plt.plot([], [], 'bo')

def init():
    ax.set_xlim(-4, 8)
    ax.set_ylim(-4, 4)
    return ln,

def update(frame):
    xdata.append(frame[0])
    ydata.append(frame[1])
    
    ln.set_data(xdata, ydata)
    return ln,

ani = FuncAnimation(fig, update, frames=X_embedded,
                    init_func=init, blit=True)
